In [2]:
import pandas as pd
import numpy as np
import openpyxl
import os
from pathlib import Path
from openpyxl import load_workbook
import re

ARCHIVO_ORIGEN = r"D:\Mateo\ICSI\Proyecto\Data\Raw\Poblacion\Data\Inputs\Censo\censo_pob_sexo_edades_quin_1993.xlsx"
AÑO_CENSO = 1993
df = pd.read_excel(ARCHIVO_ORIGEN)
# CÓDIGO DE DEPURACIÓN - Ver contenido real
print("=== DEPURACIÓN - CONTENIDO REAL ===")
print(f"Shape del DataFrame: {df.shape}")

# Mostrar las primeras 50 filas con el contenido exacto
for i in range(min(50, len(df))):
    fila_info = []
    for col in range(min(6, len(df.columns))):  # Primeras 6 columnas
        valor = df.iloc[i, col]
        if pd.isna(valor):
            fila_info.append("NaN")
        else:
            fila_info.append(f"'{str(valor).strip()}'")
    
    print(f"Fila {i}: [{', '.join(fila_info)}]")

# Buscar específicamente los patrones que necesitamos
print("\n=== BUSCANDO PATRONES ESPECÍFICOS ===")
patrones = ['AREA', 'Edades', 'HOMBRES', 'MUJERES', 'Total', '0-4', '5-9', '10-14']

for i in range(min(100, len(df))):
    for col in range(min(6, len(df.columns))):
        valor = df.iloc[i, col]
        if not pd.isna(valor):
            valor_str = str(valor).strip()
            for patron in patrones:
                if patron in valor_str:
                    print(f"Fila {i}, Col {col}: '{valor_str}'")
import pandas as pd
import numpy as np
import re

def procesar_censo_corregido(df):
    """
    Versión corregida basada en la estructura real
    """
    datos = []
    ubigeo_actual = ""
    depto_actual = ""
    
    print("🔍 Iniciando procesamiento corregido...")
    
    for i in range(len(df)):
        # Verificar fila actual para debug
        if i < 50:  # Solo debug para primeras filas
            fila_str = " | ".join([f"'{str(df.iloc[i, j]).strip()}'" if pd.notna(df.iloc[i, j]) else "NaN" 
                                  for j in range(min(5, len(df.columns)))])
            print(f"Fila {i}: {fila_str}")
        
        # 1. Buscar ÁREA - ahora buscando en todas las columnas
        for col in range(len(df.columns)):
            if pd.notna(df.iloc[i, col]):
                valor = str(df.iloc[i, col]).strip()
                if 'AREA' in valor:
                    print(f"✅ ENCONTRADO AREA en fila {i}, col {col}: '{valor}'")
                    
                    # Extraer ubigeo
                    ubigeo_match = re.search(r'(\d{6})', valor)
                    if ubigeo_match:
                        ubigeo_actual = ubigeo_match.group(1)
                    
                    # Buscar departamento en columnas adyacentes
                    for dep_col in range(col + 1, min(col + 3, len(df.columns))):
                        if pd.notna(df.iloc[i, dep_col]):
                            depto_actual = str(df.iloc[i, dep_col]).strip()
                            break
                    
                    print(f"   Ubigeo: {ubigeo_actual}, Depto: {depto_actual}")
                    break
        
        # 2. Buscar ENCABEZADOS de tabla
        for col in range(len(df.columns)):
            if pd.notna(df.iloc[i, col]):
                valor = str(df.iloc[i, col]).strip()
                if 'Edades' in valor or 'Edad' in valor:
                    print(f"✅ ENCONTRADO EDADES en fila {i}, col {col}")
                    
                    # Buscar fila de encabezados de sexo (normalmente siguiente fila)
                    if i + 1 < len(df):
                        for sexo_col in range(len(df.columns)):
                            if pd.notna(df.iloc[i + 1, sexo_col]):
                                sexo_valor = str(df.iloc[i + 1, sexo_col]).strip()
                                if 'HOMBRES' in sexo_valor:
                                    print(f"✅ ENCONTRADO HOMBRES en fila {i+1}, col {sexo_col}")
                                    
                                    # Procesar filas de datos
                                    for j in range(i + 2, min(i + 50, len(df))):
                                        # Verificar si es fin de bloque
                                        if pd.notna(df.iloc[j, 0]) and 'AREA' in str(df.iloc[j, 0]):
                                            break
                                        
                                        # Buscar datos de edad
                                        for edad_col in range(len(df.columns)):
                                            if pd.notna(df.iloc[j, edad_col]):
                                                edad_valor = str(df.iloc[j, edad_col]).strip()
                                                
                                                # Verificar si es rango de edad
                                                if (re.search(r'\d+-\d+', edad_valor) or 
                                                    '80 y más' in edad_valor or
                                                    '80 y mas' in edad_valor):
                                                    
                                                    print(f"📊 Procesando edad: '{edad_valor}' en fila {j}, col {edad_col}")
                                                    
                                                    # Formatear grupo de edad
                                                    if '-' in edad_valor:
                                                        inicio, fin = edad_valor.split('-')
                                                        grupo_edad = f"De {inicio} a {fin} años"
                                                    elif '80 y más' in edad_valor or '80 y mas' in edad_valor:
                                                        grupo_edad = "De 80 a más años"
                                                    else:
                                                        continue
                                                    
                                                    # Procesar valores (columnas a la derecha)
                                                    for valor_col in range(edad_col + 1, min(edad_col + 4, len(df.columns))):
                                                        if pd.notna(df.iloc[j, valor_col]):
                                                            try:
                                                                valor_str = re.sub(r'[^\d]', '', str(df.iloc[j, valor_col]))
                                                                if valor_str:
                                                                    valor_num = float(valor_str)
                                                                    
                                                                    # Determinar sexo por posición relativa
                                                                    sexo = ""
                                                                    if valor_col == edad_col + 1:
                                                                        sexo = "Hombre"
                                                                    elif valor_col == edad_col + 2:
                                                                        sexo = "Mujer"
                                                                    elif valor_col == edad_col + 3:
                                                                        sexo = "Total"
                                                                    
                                                                    datos.append({
                                                                        'Ubigeo': ubigeo_actual,
                                                                        'Departamento': depto_actual,
                                                                        'grupo_edad': grupo_edad,
                                                                        'sexo': sexo,
                                                                        'valor': valor_num
                                                                    })
                                                                    print(f"   ✅ {sexo}: {valor_num}")
                                                            except:
                                                                continue
                                                    
                                                    break
                                        # Salir si encontramos total
                                        if any(pd.notna(df.iloc[j, col]) and 'Total' in str(df.iloc[j, col]) 
                                               for col in range(len(df.columns))):
                                            break
                                    
                                    break
                    break
    
    return pd.DataFrame(datos)

# Ejecutar con depuración
print("🚀 Ejecutando versión corregida con depuración...")
df_corregido = procesar_censo_corregido(df)

if not df_corregido.empty:
    print(f"🎉 ¡ÉXITO! {len(df_corregido)} registros procesados")
    print(df_corregido.head(10))
else:
    print("❌ Sigue vacío. Necesito ver el output de la depuración para ayudarte mejor.")
import os
df_corregido['Anio'] = 1993 
df_corregido['Ubigeo'] = df_corregido['Ubigeo'].astype(str)

ruta_destino = r"D:\Mateo\ICSI\Proyecto\Data\Raw\Poblacion\Data\Processing"
nombre_archivo = "pob_censo_edades_sexo_1993.csv"
ruta_completa = os.path.join(ruta_destino, nombre_archivo)
df_corregido.to_csv(ruta_completa, index=False, encoding='latin1')

=== DEPURACIÓN - CONTENIDO REAL ===
Shape del DataFrame: (41231, 4)
Fila 0: [NaN, NaN, NaN, NaN]
Fila 1: ['AREA # 010101', 'CHACHAPOYAS', NaN, NaN]
Fila 2: [NaN, NaN, NaN, NaN]
Fila 3: ['Edades Quinquenales', 'Sexo', NaN, NaN]
Fila 4: [NaN, 'HOMBRES', 'MUJERES', 'Total']
Fila 5: ['0-4', '972', '941', '1913']
Fila 6: ['5-9', '1040', '1031', '2071']
Fila 7: ['10-14', '1083', '1091', '2174']
Fila 8: ['15-19', '922', '1105', '2027']
Fila 9: ['20-24', '793', '973', '1766']
Fila 10: ['25-29', '611', '778', '1389']
Fila 11: ['30-34', '539', '674', '1213']
Fila 12: ['35-39', '458', '517', '975']
Fila 13: ['40-44', '386', '450', '836']
Fila 14: ['45-49', '349', '381', '730']
Fila 15: ['50-54', '297', '329', '626']
Fila 16: ['55-59', '233', '242', '475']
Fila 17: ['60-64', '184', '224', '408']
Fila 18: ['65-69', '117', '173', '290']
Fila 19: ['70-74', '81', '126', '207']
Fila 20: ['75-79', '76', '75', '151']
Fila 21: ['80 y más', '66', '130', '196']
Fila 22: ['Total', '8207', '9240', '17447']
Fi